In [67]:
import re
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.patches as mpatches
import seaborn as sns
from datetime import datetime as dt
import folium


plt.style.use('ggplot')
pd.set_option('display.float_format', lambda x: '%.2f' % x)

In [68]:
# Import the Geopandas library to read and visualize spatial data
import geopandas as gpd

# Use the Contextily for layering
import contextily as ctx
from contextily import Place
import xyzservices.providers as xyz

## The goal is to plot an interactive on the Rhode Island's rent burden and eviction data by zip code

###  Census data and eviction data

* From [Census Reporter](https://censusreporter.org):
** Gross Rent as a Percentage of Household Income in the Past 12 Months 
** Occupied Housing Units (Owner Occupied vs Renter Occupied) 
** Median Household Income in the Past 12 Months (In 2021 Inflation-adjusted Dollars)

* From [The Eviction Lab at Princeton](https://evictionlab.org/):
** eviction filing

In [69]:
rent_gdf = gpd.read_file("/Users/keenan/Desktop/Codes/Geospatial/Rhode Island housing /RI housing analysis_12-20-2023/raw data/Rhode-Island-rent-burden-map/acs2022_5yr_B25070_14000US44007012801/acs2022_5yr_B25070_14000US44007012801.geojson")
rent_gdf.head()

geoid                           name  B25070001   
0           04000US44                   Rhode Island  161269.00  \
1  14000US44001030100  Census Tract 301, Bristol, RI     231.00   
2  14000US44001030200  Census Tract 302, Bristol, RI     264.00   
3  14000US44001030300  Census Tract 303, Bristol, RI     124.00   
4  14000US44001030400  Census Tract 304, Bristol, RI      51.00   

   B25070001, Error  B25070002  B25070002, Error  B25070003  B25070003, Error   
0           2231.00    7362.00            833.00   12611.00            904.00  \
1             85.00       0.00             14.00      16.00             26.00   
2            101.00      21.00             25.00      38.00             33.00   
3             67.00       6.00             13.00       0.00             14.00   
4             42.00       0.00             14.00       0.00             14.00   

   B25070004  B25070004, Error  ...  B25070007, Error  B25070008   
0   20165.00           1455.00  ...           1142.00    9402.00  \
1      40.00             47.00  ...             28.00      46.00   
2      42.00             41.00  ...             15.00      38.00   
3      44.00             44.00  ...             14.00       0.00   
4      31.00             35.00  ...             14.00       0.00   

   B25070008, Error  B25070009  B25070009, Error  B25070010  B25070010, Error   
0            928.00   12741.00           1105.00   35315.00           1652.00  \
1             42.00      19.00             17.00      63.00             45.00   
2             40.00       4.00              8.00      65.00             62.00   
3             14.00      12.00             19.00      21.00             25.00   
4             14.00       0.00             14.00       0.00             14.00   

   B25070011  B25070011, Error   
0    8906.00            829.00  \
1       9.00             20.00   
2      31.00             19.00   
3      22.00             25.00   
4       6.00             10.00   

                                            geometry  
0  MULTIPOLYGON (((-71.78970 41.72520, -71.78971 ...  
1  MULTIPOLYGON (((-71.36521 41.73565, -71.36020 ...  
2  MULTIPOLYGON (((-71.33266 41.76572, -71.33200 ...  
3  MULTIPOLYGON (((-71.31995 41.77451, -71.31954 ...  
4  MULTIPOLYGON (((-71.35508 41.72696, -71.34122 ...  

[5 rows x 25 columns]

In [70]:
# Drop columns containing string "error" in their titles
rent_gdf = rent_gdf[rent_gdf.columns.drop(list(rent_gdf.filter(regex='Error')))]
rent_gdf.columns

Index(['geoid', 'name', 'B25070001', 'B25070002', 'B25070003', 'B25070004',
       'B25070005', 'B25070006', 'B25070007', 'B25070008', 'B25070009',
       'B25070010', 'B25070011', 'geometry'],
      dtype='object')

In [71]:
# From the Census documentation, we know the column "name" seems to the zip codes,
# and the various "Bxxxxx" refer to rent/income ratio,
# renaming the columns
rent_gdf.columns = ['geoid',
               'census tract',
               "total respondents",
               "less than 10.0 percent",
               "10.0 to 14.9 percent",
               "15.0 to 19.9 percent",
               "20.0 to 24.9 percent",
               "25.0 to 29.9 percent",
               "30.0 to 34.9 percent",
               "35.0 to 39.9 percent",
               "40.0 to 49.9 percent",
               "50.0 percent or more",
               "not computed",
               "geometry"
              ]

rent_gdf.columns

Index(['geoid', 'census tract', 'total respondents', 'less than 10.0 percent',
       '10.0 to 14.9 percent', '15.0 to 19.9 percent', '20.0 to 24.9 percent',
       '25.0 to 29.9 percent', '30.0 to 34.9 percent', '35.0 to 39.9 percent',
       '40.0 to 49.9 percent', '50.0 percent or more', 'not computed',
       'geometry'],
      dtype='object')

In [72]:
# Convert columns[3:13] from nominal number to percentage of the total respondents

rent_gdf.iloc[:, 3:13] = rent_gdf.iloc[:, 3:13].div(rent_gdf['total respondents'], axis=0).round(2)
rent_gdf.head()

geoid                   census tract  total respondents   
0           04000US44                   Rhode Island          161269.00  \
1  14000US44001030100  Census Tract 301, Bristol, RI             231.00   
2  14000US44001030200  Census Tract 302, Bristol, RI             264.00   
3  14000US44001030300  Census Tract 303, Bristol, RI             124.00   
4  14000US44001030400  Census Tract 304, Bristol, RI              51.00   

   less than 10.0 percent  10.0 to 14.9 percent  15.0 to 19.9 percent   
0                    0.05                  0.08                  0.13  \
1                    0.00                  0.07                  0.17   
2                    0.08                  0.14                  0.16   
3                    0.05                  0.00                  0.35   
4                    0.00                  0.00                  0.61   

   20.0 to 24.9 percent  25.0 to 29.9 percent  30.0 to 34.9 percent   
0                  0.13                  0.12                  0.09  \
1                  0.00                  0.03                  0.13   
2                  0.06                  0.00                  0.04   
3                  0.15                  0.00                  0.00   
4                  0.27                  0.00                  0.00   

   35.0 to 39.9 percent  40.0 to 49.9 percent  50.0 percent or more   
0                  0.06                  0.08                  0.22  \
1                  0.20                  0.08                  0.27   
2                  0.14                  0.02                  0.25   
3                  0.00                  0.10                  0.17   
4                  0.00                  0.00                  0.00   

   not computed                                           geometry  
0          0.06  MULTIPOLYGON (((-71.78970 41.72520, -71.78971 ...  
1          0.04  MULTIPOLYGON (((-71.36521 41.73565, -71.36020 ...  
2          0.12  MULTIPOLYGON (((-71.33266 41.76572, -71.33200 ...  
3          0.18  MULTIPOLYGON (((-71.31995 41.77451, -71.31954 ...  
4          0.12  MULTIPOLYGON (((-71.35508 41.72696, -71.34122 ...

In [73]:
# Inspect data validity 

rent_gdf[rent_gdf.isna()].count()

geoid                     0
census tract              0
total respondents         0
less than 10.0 percent    0
10.0 to 14.9 percent      0
15.0 to 19.9 percent      0
20.0 to 24.9 percent      0
25.0 to 29.9 percent      0
30.0 to 34.9 percent      0
35.0 to 39.9 percent      0
40.0 to 49.9 percent      0
50.0 percent or more      0
not computed              0
geometry                  0
dtype: int64

In [74]:
# how many "not computed" out there?
rent_gdf["not computed"].describe()

count   246.00
mean      0.07
std       0.10
min       0.00
25%       0.01
50%       0.04
75%       0.08
max       0.71
Name: not computed, dtype: float64

In [75]:
# There's no available data on the zip code 02812

rent_gdf[rent_gdf["Not computed"] == rent_gdf["Not computed"].max()]

KeyError: 'Not computed'

In [76]:
thirty_plus = rent_gdf.iloc[:, 8:12]

# Create a column called "rent-burdened population," aka those paying 30 percent or more of their income
rent_gdf["rent burden"] = thirty_plus.sum(axis=1)

# Also create a column called "severe rent-burdened population", aka "50.0 percent or more"
rent_gdf["severe rent burden"] = rent_gdf["50.0 percent or more"]

rent_gdf.head()

geoid                   census tract  total respondents   
0           04000US44                   Rhode Island          161269.00  \
1  14000US44001030100  Census Tract 301, Bristol, RI             231.00   
2  14000US44001030200  Census Tract 302, Bristol, RI             264.00   
3  14000US44001030300  Census Tract 303, Bristol, RI             124.00   
4  14000US44001030400  Census Tract 304, Bristol, RI              51.00   

   less than 10.0 percent  10.0 to 14.9 percent  15.0 to 19.9 percent   
0                    0.05                  0.08                  0.13  \
1                    0.00                  0.07                  0.17   
2                    0.08                  0.14                  0.16   
3                    0.05                  0.00                  0.35   
4                    0.00                  0.00                  0.61   

   20.0 to 24.9 percent  25.0 to 29.9 percent  30.0 to 34.9 percent   
0                  0.13                  0.12                  0.09  \
1                  0.00                  0.03                  0.13   
2                  0.06                  0.00                  0.04   
3                  0.15                  0.00                  0.00   
4                  0.27                  0.00                  0.00   

   35.0 to 39.9 percent  40.0 to 49.9 percent  50.0 percent or more   
0                  0.06                  0.08                  0.22  \
1                  0.20                  0.08                  0.27   
2                  0.14                  0.02                  0.25   
3                  0.00                  0.10                  0.17   
4                  0.00                  0.00                  0.00   

   not computed                                           geometry   
0          0.06  MULTIPOLYGON (((-71.78970 41.72520, -71.78971 ...  \
1          0.04  MULTIPOLYGON (((-71.36521 41.73565, -71.36020 ...   
2          0.12  MULTIPOLYGON (((-71.33266 41.76572, -71.33200 ...   
3          0.18  MULTIPOLYGON (((-71.31995 41.77451, -71.31954 ...   
4          0.12  MULTIPOLYGON (((-71.35508 41.72696, -71.34122 ...   

   rent burden  severe rent burden  
0         0.45                0.22  
1         0.68                0.27  
2         0.45                0.25  
3         0.27                0.17  
4         0.00                0.00

### The above table tells us that:
#### 1) 45 percent of the renters experience rent burdens in 2022; 
#### 2) 22 percent were severely rent burdened. 

In [77]:
# Drop the first row, which are the stats for the entire state, according to the documentation

rent_gdf = rent_gdf.drop([0]).copy()
rent_gdf.head()

geoid                   census tract  total respondents   
1  14000US44001030100  Census Tract 301, Bristol, RI             231.00  \
2  14000US44001030200  Census Tract 302, Bristol, RI             264.00   
3  14000US44001030300  Census Tract 303, Bristol, RI             124.00   
4  14000US44001030400  Census Tract 304, Bristol, RI              51.00   
5  14000US44001030500  Census Tract 305, Bristol, RI            1216.00   

   less than 10.0 percent  10.0 to 14.9 percent  15.0 to 19.9 percent   
1                    0.00                  0.07                  0.17  \
2                    0.08                  0.14                  0.16   
3                    0.05                  0.00                  0.35   
4                    0.00                  0.00                  0.61   
5                    0.03                  0.12                  0.11   

   20.0 to 24.9 percent  25.0 to 29.9 percent  30.0 to 34.9 percent   
1                  0.00                  0.03                  0.13  \
2                  0.06                  0.00                  0.04   
3                  0.15                  0.00                  0.00   
4                  0.27                  0.00                  0.00   
5                  0.05                  0.06                  0.14   

   35.0 to 39.9 percent  40.0 to 49.9 percent  50.0 percent or more   
1                  0.20                  0.08                  0.27  \
2                  0.14                  0.02                  0.25   
3                  0.00                  0.10                  0.17   
4                  0.00                  0.00                  0.00   
5                  0.06                  0.07                  0.28   

   not computed                                           geometry   
1          0.04  MULTIPOLYGON (((-71.36521 41.73565, -71.36020 ...  \
2          0.12  MULTIPOLYGON (((-71.33266 41.76572, -71.33200 ...   
3          0.18  MULTIPOLYGON (((-71.31995 41.77451, -71.31954 ...   
4          0.12  MULTIPOLYGON (((-71.35508 41.72696, -71.34122 ...   
5          0.07  MULTIPOLYGON (((-71.28980 41.73381, -71.28943 ...   

   rent burden  severe rent burden  
1         0.68                0.27  
2         0.45                0.25  
3         0.27                0.17  
4         0.00                0.00  
5         0.55                0.28

In [78]:
rent_gdf.columns

Index(['geoid', 'census tract', 'total respondents', 'less than 10.0 percent',
       '10.0 to 14.9 percent', '15.0 to 19.9 percent', '20.0 to 24.9 percent',
       '25.0 to 29.9 percent', '30.0 to 34.9 percent', '35.0 to 39.9 percent',
       '40.0 to 49.9 percent', '50.0 percent or more', 'not computed',
       'geometry', 'rent burden', 'severe rent burden'],
      dtype='object')

In [79]:
# Keep only zip code, total respondents, geometry, rent burden and severe rent burden columns

keep_cols = ["geoid", 'census tract', 'total respondents', "geometry", "rent burden", "severe rent burden"]
rent_gdf = rent_gdf[keep_cols]

In [80]:
# Top rent-burdened Rhode Island zip codes 
rent_gdf.sort_values(by='rent burden', ascending=False).head(10)

geoid                         census tract   
125  14000US44007010701  Census Tract 107.01, Providence, RI  \
135  14000US44007011403  Census Tract 114.03, Providence, RI   
36   14000US44003021501        Census Tract 215.01, Kent, RI   
238  14000US44009051102  Census Tract 511.02, Washington, RI   
52   14000US44005040102     Census Tract 401.02, Newport, RI   
28   14000US44003020904        Census Tract 209.04, Kent, RI   
66   14000US44005041100        Census Tract 411, Newport, RI   
45   14000US44003022100           Census Tract 221, Kent, RI   
56   14000US44005040302     Census Tract 403.02, Newport, RI   
179  14000US44007014300     Census Tract 143, Providence, RI   

     total respondents                                           geometry   
125             250.00  MULTIPOLYGON (((-71.35511 41.77458, -71.35510 ...  \
135             513.00  MULTIPOLYGON (((-71.48724 41.97921, -71.48720 ...   
36              422.00  MULTIPOLYGON (((-71.38926 41.72761, -71.38590 ...   
238             252.00  MULTIPOLYGON (((-71.64874 41.42122, -71.64870 ...   
52              389.00  MULTIPOLYGON (((-71.26566 41.53827, -71.26557 ...   
28              103.00  MULTIPOLYGON (((-71.49569 41.60268, -71.49563 ...   
66              399.00  MULTIPOLYGON (((-71.33241 41.48674, -71.33198 ...   
45              352.00  MULTIPOLYGON (((-71.49049 41.70977, -71.49008 ...   
56              189.00  MULTIPOLYGON (((-71.31096 41.51942, -71.31092 ...   
179             652.00  MULTIPOLYGON (((-71.47323 41.76732, -71.47294 ...   

     rent burden  severe rent burden  
125         0.82                0.46  
135         0.74                0.50  
36          0.74                0.22  
238         0.73                0.38  
52          0.73                0.52  
28          0.73                0.63  
66          0.72                0.13  
45          0.70                0.34  
56          0.69                0.46  
179         0.69                0.35

In [86]:
# To understand the distribution of renters in the Rhode Island by
# by analyzing data on housing occupancy by tenure 


tenant_gdf = gpd.read_file("/Users/keenan/Desktop/Codes/Geospatial/Rhode Island housing /RI housing analysis_12-20-2023/raw data/Rhode-Island-rent-burden-map/acs2022_5yr_B25008_14000US44007012801/acs2022_5yr_B25008_14000US44007012801.geojson")
tenant_gdf.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 251 entries, 0 to 250
Data columns (total 9 columns):
 #   Column            Non-Null Count  Dtype   
---  ------            --------------  -----   
 0   geoid             251 non-null    object  
 1   name              251 non-null    object  
 2   B25008001         251 non-null    float64 
 3   B25008001, Error  251 non-null    float64 
 4   B25008002         251 non-null    float64 
 5   B25008002, Error  251 non-null    float64 
 6   B25008003         251 non-null    float64 
 7   B25008003, Error  251 non-null    float64 
 8   geometry          251 non-null    geometry
dtypes: float64(6), geometry(1), object(2)
memory usage: 17.8+ KB


In [87]:
tenant_gdf.head()

geoid                           name  B25008001   
0           04000US44                   Rhode Island 1049253.00  \
1  14000US44001030100  Census Tract 301, Bristol, RI    4719.00   
2  14000US44001030200  Census Tract 302, Bristol, RI    3365.00   
3  14000US44001030300  Census Tract 303, Bristol, RI    4622.00   
4  14000US44001030400  Census Tract 304, Bristol, RI    4296.00   

   B25008001, Error  B25008002  B25008002, Error  B25008003  B25008003, Error   
0     -555555600.00  701567.00           6627.00  347686.00           6627.00  \
1            482.00    4105.00            462.00     614.00            343.00   
2            398.00    2818.00            431.00     547.00            186.00   
3            389.00    4352.00            436.00     270.00            178.00   
4            483.00    4112.00            509.00     184.00            160.00   

                                            geometry  
0  MULTIPOLYGON (((-71.78970 41.72520, -71.78971 ...  
1  MULTIPOLYGON (((-71.36521 41.73565, -71.36020 ...  
2  MULTIPOLYGON (((-71.33266 41.76572, -71.33200 ...  
3  MULTIPOLYGON (((-71.31995 41.77451, -71.31954 ...  
4  MULTIPOLYGON (((-71.35508 41.72696, -71.34122 ...

In [91]:
tenant_gdf.columns

Index(['geoid', 'name', 'B25008001', 'B25008001, Error', 'B25008002',
       'B25008002, Error', 'B25008003', 'B25008003, Error', 'geometry'],
      dtype='object')

In [92]:
# Simiarily, keep only the useful columns and rows 

columns_to_keep =  ['geoid',
                    'name',
                    'B25008001', 
                    'B25008002',
                    'B25008003',
                    'geometry'
                   ]

tenant_gdf = tenant_gdf[columns_to_keep]

# rename columns
tenant_gdf.columns = ['geoid',
                      'census tract',
                       "total units",
                       "owner occupied",
                       "renter occupied",
                      'geometry'
                    ]

tenant_gdf.info()

<class 'geopandas.geodataframe.GeoDataFrame'>
RangeIndex: 251 entries, 0 to 250
Data columns (total 6 columns):
 #   Column           Non-Null Count  Dtype   
---  ------           --------------  -----   
 0   geoid            251 non-null    object  
 1   census tract     251 non-null    object  
 2   total units      251 non-null    float64 
 3   owner occupied   251 non-null    float64 
 4   renter occupied  251 non-null    float64 
 5   geometry         251 non-null    geometry
dtypes: float64(3), geometry(1), object(2)
memory usage: 11.9+ KB


In [93]:
# Calculat the percentages of owener and renter occupied units 
# and store them in two new columns

tenant_gdf['owner occupied percentage'] = tenant_gdf['owner occupied']/tenant_gdf['total units']
tenant_gdf['renter occupied percentage'] = tenant_gdf['renter occupied']/tenant_gdf['total units']



# Drop first row again
tenant_gdf = tenant_gdf.drop([0])

tenant_gdf.head()

/Users/keenan/opt/anaconda3/lib/python3.9/site-packages/geopandas/geodataframe.py:1543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)
/Users/keenan/opt/anaconda3/lib/python3.9/site-packages/geopandas/geodataframe.py:1543: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  super().__setitem__(key, value)


geoid                   census tract  total units   
1  14000US44001030100  Census Tract 301, Bristol, RI      4719.00  \
2  14000US44001030200  Census Tract 302, Bristol, RI      3365.00   
3  14000US44001030300  Census Tract 303, Bristol, RI      4622.00   
4  14000US44001030400  Census Tract 304, Bristol, RI      4296.00   
5  14000US44001030500  Census Tract 305, Bristol, RI      3172.00   

   owner occupied  renter occupied   
1         4105.00           614.00  \
2         2818.00           547.00   
3         4352.00           270.00   
4         4112.00           184.00   
5         1389.00          1783.00   

                                            geometry   
1  MULTIPOLYGON (((-71.36521 41.73565, -71.36020 ...  \
2  MULTIPOLYGON (((-71.33266 41.76572, -71.33200 ...   
3  MULTIPOLYGON (((-71.31995 41.77451, -71.31954 ...   
4  MULTIPOLYGON (((-71.35508 41.72696, -71.34122 ...   
5  MULTIPOLYGON (((-71.28980 41.73381, -71.28943 ...   

   owner occupied percentage  renter occupied percentage  
1                       0.87                        0.13  
2                       0.84                        0.16  
3                       0.94                        0.06  
4                       0.96                        0.04  
5                       0.44                        0.56

In [18]:
# Because the previous occupancy data is drawn from surveys, 
# in order to calculate a "ballpark" number of renter population,
# it's necessary to cross-reference the total population per census tract data

pop_df = pd.read_csv(
             file_path+'total pouplation.csv',
             index_col=False

    )
pop_df.head()

geoid          name  B01003001  B01003001, Error
0     04000US44  Rhode Island    1094250        -555555600
1  86000US02802         02802        702               407
2  86000US02804         02804       2560               630
3  86000US02806         02806      17121                33
4  86000US02807         02807        962               232

In [19]:
# Same old, dropping unimportant columns and rows

pop_df = pop_df[['name', 'B01003001']].rename(columns={"name":"zip code", "B01003001":"population"})
pop_df = pop_df.drop([0])
pop_df.head()

zip code  population
1    02802         702
2    02804        2560
3    02806       17121
4    02807         962
5    02808        2328

In [20]:
# Merge with tenant_gdf
tenant_gdf = pd.merge(tenant_gdf, pop_df, on='zip code')

# Calculate the estimated renting population 
tenant_gdf["estimated renting population"] = round(tenant_gdf['renter occupied percentage']\
                                         * tenant_gdf["population"])

tenant_gdf.head()

geoid zip code  total units  owner occupied  renter occupied   
0  86000US02802    02802       238.00           58.00           180.00  \
1  86000US02804    02804       898.00          738.00           160.00   
2  86000US02806    02806      6176.00         5500.00           676.00   
3  86000US02807    02807       459.00          338.00           121.00   
4  86000US02808    02808       901.00          512.00           389.00   

                                            geometry   
0  MULTIPOLYGON (((-71.46290 41.95716, -71.46286 ...  \
1  MULTIPOLYGON (((-71.80320 41.40433, -71.80277 ...   
2  MULTIPOLYGON (((-71.36521 41.73565, -71.36020 ...   
3  MULTIPOLYGON (((-71.61418 41.16117, -71.61266 ...   
4  MULTIPOLYGON (((-71.78108 41.39324, -71.78101 ...   

   owner occupied percentage  renter occupied percentage  population   
0                       0.24                        0.76         702  \
1                       0.82                        0.18        2560   
2                       0.89                        0.11       17121   
3                       0.74                        0.26         962   
4                       0.57                        0.43        2328   

   estimated renting population  
0                        531.00  
1                        456.00  
2                       1874.00  
3                        254.00  
4                       1005.00

In [21]:
# To plot density by dots would require turning the multipolygon objects into centroid ones
# through Geopandas' ().centroid method

tenant_centroid = tenant_gdf.copy()
tenant_centroid['geometry'] = tenant_centroid['geometry'].centroid
tenant_centroid.head()

/var/folders/9l/mpkqkhbx2dv2q05jtmjfhwk40000gp/T/ipykernel_7659/3415760032.py:5: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  tenant_centroid['geometry'] = tenant_centroid['geometry'].centroid


geoid zip code  total units  owner occupied  renter occupied   
0  86000US02802    02802       238.00           58.00           180.00  \
1  86000US02804    02804       898.00          738.00           160.00   
2  86000US02806    02806      6176.00         5500.00           676.00   
3  86000US02807    02807       459.00          338.00           121.00   
4  86000US02808    02808       901.00          512.00           389.00   

                     geometry  owner occupied percentage   
0  POINT (-71.45535 41.95188)                       0.24  \
1  POINT (-71.77238 41.43186)                       0.82   
2  POINT (-71.31929 41.73425)                       0.89   
3  POINT (-71.57829 41.17834)                       0.74   
4  POINT (-71.74864 41.40859)                       0.57   

   renter occupied percentage  population  estimated renting population  
0                        0.76         702                        531.00  
1                        0.18        2560                        456.00  
2                        0.11       17121                       1874.00  
3                        0.26         962                        254.00  
4                        0.43        2328                       1005.00

In [22]:
type(tenant_centroid.geometry)

geopandas.geoseries.GeoSeries

In [25]:
m = rent_gdf.explore(
    column= "rent burden",
    tooltip = 'zip code',
    popup=True,
    scheme="percentiles",
    alpha = 0.5,
    linewidth= 2,
    cmap = 'coolwarm',
    name = 'Rent Burden (30 percent or more of household income)',
    tiles = ctx.providers.CartoDB.Voyager,
    
    

                    )

rent_gdf.explore(
     m=m,
     tooltip = 'zip code',
     column= "severe rent burden",
     scheme="percentiles",
     name = 'Severe Rent Burden (50 percent or more of household income)',
     alpha = 0.5,
     popup=True,
     cmap='bwr'
                    )



                        
                    

folium.TileLayer("CartoDB positron", show=True).add_to(m)

folium.LayerControl().add_to(m) 

from folium.plugins import Geocoder

Geocoder().add_to(m)

m

In [26]:
import pandas as pd
from dbfread import DBF

for record in DBF('/Users/keenan/Downloads/tl_2020_44_tract/tl_2020_44_tract.dbf'):
    print(record)

table = DBF('/Users/keenan/Downloads/tl_2020_44_tract/tl_2020_44_tract.dbf', load=True)
print(table.records[1])

from simpledbf import Dbf5

dbf = Dbf5('/Users/keenan/Downloads/tl_2020_44_tract/tl_2020_44_tract.dbf')
df = dbf.to_dataframe()

df.info()

df.head()

df.sort_values(by='GEOID')

df[["COUNTYFP", "GEOID", "INTPTLAT", "INTPTLON" ]]

df[df.NAMELSAD.str.contains("506")]

df.nunique()

import geopandas as gpd
from shapely.geometry import Point

gdf = gpd.GeoDataFrame(df)
gdf.head()

geometry = [Point(lon, lat) for lon, lat in zip(df['INTPTLON'], df['INTPTLAT'])]
gdf = gpd.GeoDataFrame(df, geometry=geometry, crs='EPSG:4326')
gdf.head()

gdf.columns = gdf.columns.str.lower()
gdf.head()

eviction_df = pd.read_csv('evictions.csv', index_col=False)
eviction_df.head()

eviction_df.nunique()

# Rename the column headers

eviction_df = eviction_df.rename(columns={"filings_2020" : "evictions", "GEOID":"geoid"})


# Drop all the sealed rows
drop_mask = eviction_df[eviction_df['geoid'] == 'sealed'].index
eviction_df = eviction_df.drop(drop_mask)
eviction_df[eviction_df['geoid'] == 'sealed']

eviction_df = pd.DataFrame(eviction_df.groupby(['geoid'])['evictions'].sum()).reset_index()
eviction_df.head()

eviction_df.info()

eviction_table = pd.merge(gdf, eviction_df, how='left', on='geoid')
eviction_table= eviction_table[['geoid', 'countyfp', 'geometry', 'evictions']]
eviction_table.head()

eviction_table.geoid.nunique()

eviction_table.info()

eviction_table[eviction_table.isna().any(axis=1)]

eviction_table[eviction_table.isna().any(axis=1)]

eviction_table = eviction_table.dropna()
eviction_table[eviction_table.isna().any(axis=1)]

eviction_table.info()

eviction_table.head()

eviction_table.explore(
    color = "gold",
    alpha=0.5,
    name = "Number of Eviction Filings (between Jan 1. 2021 to Nov. 30, 2023)",
    style_kwds={"style_function":lambda x: {"radius":x["properties"]["evictions"]/100}} 
                        )




import contextily as ctx
from contextily import Place
import xyzservices.providers as xyz
import folium







# The Princeton eviction dataset uses the 11-digit FIPS code, 
# whereas the other Census datasets examined here use the 12-digit ones (***** + zip codes).
# Hence, cross-reference HUD-USPS ZIP Crosswalk Files


zip_tract = pd.read_excel('/Users/keenan/Desktop/Codes/Geospatial/TRACT_ZIP_092023.xlsx', 
                          index_col=False
                         )
             
                          
                    

zip_tract.info()

zip_tract.head()

# This is a large dataset and reflected in the amount of time it took to import
# Slice out the Rhode Island data
zip_tract = zip_tract[zip_tract['USPS_ZIP_PREF_STATE'] == 'RI'] 

# Complete Rhode Island zip codes by adding "0" 
# and also convert them from integers to strings
zip_tract['ZIP'] = "0" + zip_tract['ZIP'].astype("string")
zip_tract['TRACT'] = zip_tract['TRACT'].astype("string")

zip_tract.info()

zip_tract.nunique()

zip_tract.columns

zip_tract = zip_tract[['TRACT', 'ZIP', 'USPS_ZIP_PREF_CITY']]

zip_tract.columns=['geoid', 'zip code', 'city' ]

zip_tract.head()

zip_tract.groupby('geoid')[['zip code', 'city']].value_counts()

zip_table = zip_tract.groupby('geoid')[['zip code', 'city']].agg(lambda x: ', '.join(map(str, x))).reset_index()
zip_table.city = zip_table.city.str.title()
zip_table.info()

zip_table.sample(10)

def remove_duplicates(city_list):
    unique_cities = []
    seen_cities = set()
    for city in city_list.split(','):
        city = city.strip()
        if city not in seen_cities:
            unique_cities.append(city)
            seen_cities.add(city)
    return ', '.join(unique_cities)

zip_table['city'] = zip_table['city'].apply(lambda x: remove_duplicates(x) if pd.notna(x) else x)
zip_table.city.sample(20)



zip_table[zip_table['zip code'].str.contains('02875')]

zip_table[zip_table.city.str.contains('Shannock')]

eviction_table.evictions.astype('int')

pd.merge(eviction_table, zip_table, on='geoid')

new_table = pd.merge(eviction_table, zip_table, on='geoid')
new_table = new_table[['geoid', 'zip code',  'evictions', 'city','geometry']]
new_table['zip code'] = new_table['zip code'].str.replace(r',', ', ')
new_table['evictions'] = new_table['evictions'].astype('int')

new_table.info()

type(new_table)

OrderedDict([('STATEFP', '44'), ('COUNTYFP', '003'), ('TRACTCE', '021002'), ('GEOID', '44003021002'), ('NAME', '210.02'), ('NAMELSAD', 'Census Tract 210.02'), ('MTFCC', 'G5020'), ('FUNCSTAT', 'S'), ('ALAND', 2706612), ('AWATER', 472653), ('INTPTLAT', '+41.7569676'), ('INTPTLON', '-071.3947778')])
OrderedDict([('STATEFP', '44'), ('COUNTYFP', '003'), ('TRACTCE', '021300'), ('GEOID', '44003021300'), ('NAME', '213'), ('NAMELSAD', 'Census Tract 213'), ('MTFCC', 'G5020'), ('FUNCSTAT', 'S'), ('ALAND', 4168478), ('AWATER', 2578903), ('INTPTLAT', '+41.7397743'), ('INTPTLON', '-071.3870958')])
OrderedDict([('STATEFP', '44'), ('COUNTYFP', '003'), ('TRACTCE', '021100'), ('GEOID', '44003021100'), ('NAME', '211'), ('NAMELSAD', 'Census Tract 211'), ('MTFCC', 'G5020'), ('FUNCSTAT', 'S'), ('ALAND', 7158162), ('AWATER', 136612), ('INTPTLAT', '+41.7424748'), ('INTPTLON', '-071.4343102')])
OrderedDict([('STATEFP', '44'), ('COUNTYFP', '003'), ('TRACTCE', '020904'), ('GEOID', '44003020904'), ('NAME', '209.0

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 188629 entries, 0 to 188628
Data columns (total 8 columns):
 #   Column               Non-Null Count   Dtype  
---  ------               --------------   -----  
 0   TRACT                188629 non-null  int64  
 1   ZIP                  188629 non-null  int64  
 2   USPS_ZIP_PREF_CITY   188629 non-null  object 
 3   USPS_ZIP_PREF_STATE  188629 non-null  object 
 4   RES_RATIO            188629 non-null  float64
 5   BUS_RATIO            188629 non-null  float64
 6   OTH_RATIO            188629 non-null  float64
 7   TOT_RATIO            188629 non-null  float64
dtypes: float64(4), int64(2), object(2)
memory usage: 11.5+ MB
<class 'pandas.core.frame.DataFrame'>
Index: 477 entries, 147497 to 147973
Data columns (total 8 columns):
 #   Column               Non-Null Count  Dtype  
---  ------               --------------  -----  
 0   TRACT                477 non-null    string 
 1   ZIP                  477 non-null    string 
 2   USPS_

geopandas.geodataframe.GeoDataFrame

In [31]:
m = rent_gdf.explore(
    column= "rent burden",
    tooltip = 'zip code',
    popup=True,
    scheme="percentiles",
    alpha = 0.5,
    linewidth= 2,
    cmap = 'coolwarm',
    name = 'Rent Burden (30 percent or more of household income)',
    tiles = ctx.providers.CartoDB.Voyager,
    
    

                    )

rent_gdf.explore(
     m=m,
     tooltip = 'zip code',
     column= "severe rent burden",
     scheme="percentiles",
     name = 'Severe Rent Burden (50 percent or more of household income)',
     alpha = 0.5,
     popup=True,
     cmap='bwr'
                    )


new_table[new_table["evictions"] > 0].explore(
    m=m,
    color = "green",
    alpha=0.5,
    name = "Number of Eviction Filings (between Jan 1. 2021 to Nov. 30, 2023)",
    style_kwds={"style_function":lambda x: {"radius":x["properties"]["evictions"]/100}} 
                        )
                        
                    

folium.TileLayer("CartoDB positron", show=True).add_to(m)

folium.LayerControl().add_to(m) 

from folium.plugins import Geocoder

Geocoder().add_to(m)

m